# Longshore plots of each beach
- Need to create a longshore plot of each beach to see how the variables change alongshore.

## Setup notebook

In [ ]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [ ]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os
import decimal
import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
from plotly import tools
import plotly.io as pio
from scipy import stats
import math
import matplotlib
from matplotlib import cm
import colorlover as cl
from tqdm import tqdm_notebook
from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML
from scipy import stats
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from scipy.interpolate import interp1d
from pandas.api.types import CategoricalDtype

In [ ]:
# Matplot lib default settings
plt.rcParams["figure.figsize"] = (10,6)
plt.rcParams['axes.grid']=True
plt.rcParams['grid.alpha'] = 0.5
plt.rcParams['grid.color'] = "grey"
plt.rcParams['grid.linestyle'] = "--"
plt.rcParams['axes.grid']=True

# https://stackoverflow.com/a/20709149
matplotlib.rcParams['text.usetex'] = True

matplotlib.rcParams['text.latex.preamble'] = [
       r'\usepackage{siunitx}',   # i need upright \micro symbols, but you need...
       r'\sisetup{detect-all}',   # ...this to force siunitx to actually use your fonts
       r'\usepackage{helvet}',    # set the normal font here
       r'\usepackage{amsmath}',
       r'\usepackage{sansmath}',  # load up the sansmath so that math -> helvet
       r'\sansmath',              # <- tricky! -- gotta actually tell tex to use!
]  

## Import data

In [ ]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_waves = df_from_csv('waves.csv', index_col=[0, 1])
df_tides = df_from_csv('tides.csv', index_col=[0, 1])
df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_sites = df_from_csv('sites.csv', index_col=[0])
df_profile_features_crest_toes = df_from_csv('profile_features_crest_toes.csv', index_col=[0,1])

# Note that the forecasted data sets should be in the same order for impacts and twls
impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }


twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}
print('Done!')

## Generate plot for each beach

In [ ]:
beach = 'NARRA'

# Get the dataframe
df = impacts['forecasted']['mean_slope_sto06']
df = df.rename(columns={'storm_regime': 'forecasted_regime'})

df_beach = df.loc[df.index.str.contains(beach)]

# Add information about hydrodynamics at max(R_high) time
df_beach = df_beach.merge(
    twls['forecasted']['mean_slope_sto06'].drop(columns=['R_high', 'R_low']),
    left_on=['site_id', 'datetime'],
    right_on=['site_id', 'datetime'])

# Add information about observed impacts
obs_impacts = impacts['observed'].rename(columns={
    'storm_regime': 'observed_regime'
}).observed_regime.to_frame()
df_beach = df_beach.merge(obs_impacts, left_on='site_id', right_on='site_id')

# Convert storm regimes to categorical datatype
cat_type = CategoricalDtype(
    categories=['swash', 'collision', 'overwash', 'inundation'], ordered=True)
df_beach.forecasted_regime = df_beach.forecasted_regime.astype(cat_type)
df_beach.observed_regime = df_beach.observed_regime.astype(cat_type)

# Get index
n = [x for x in range(len(df_beach))][::-1]
n_sites = [x for x in df_beach.index][::-1]

f, (ax1, ax2, ax3, ax4, ax5, ax6, ax7, ax8) = plt.subplots(
    1,
    8,
    sharey=True,
    figsize=(14, 8),
    gridspec_kw={'width_ratios': [4, 4, 2, 2, 2, 2,2,2]})

# Specify colors for storm regimes
cmap = {
    'swash': '#1a9850',
    'collision': '#fee08b',
    'overwash': '#d73027'
}

colors = [cmap.get(x) for x in df_beach.observed_regime]
colors = ['#d73027' if c is None else c for c in colors]

# Plot forecasted and observed storm regime
ax1.scatter(
    df_beach.observed_regime.cat.codes.replace(-1,np.NaN),
    n,
    color=colors,
    marker='o',
    label='Observed regime')

ax1.scatter(
    df_beach.forecasted_regime.cat.codes.replace(-1,np.NaN),
    n,
    color='b',
    marker='o',
    edgecolors='black',
    facecolors='none',
    label='Forecasted regime')

ax1.set_title('Storm\nregime')
ax1.set_xticks([0,1,2,3])
ax1.set_xticklabels(['swash','collision','overwash','inundation'])
ax1.tick_params(axis='x', rotation=45)
ax1.legend(loc='center', bbox_to_anchor=(0.5, -0.15))

# Replace yticks with site_ids
yticks = ax1.get_yticks().tolist()
yticks = [n_sites[int(y)] if 0 <= y <= len(n_sites) else y for y in yticks ]
ax1.set_yticklabels(yticks)

# Water levels
ax2.plot(df_beach.R_high, n, color='#2c7bb6')
ax2.plot(df_beach.R_low, n, color='#2c7bb6')
ax2.fill_betweenx(
    n, df_beach.R_low, df_beach.R_high, alpha=0.2, color='#2c7bb6', label='$R_{low}$ to $R_{high}$')

# Dune elevations
ax2.plot(df_beach.dune_crest_z, n, color='#fdae61')
ax2.plot(df_beach.dune_toe_z, n, color='#fdae61')
ax2.fill_betweenx(
    n, df_beach.dune_toe_z, df_beach.dune_crest_z, alpha=0.2, color='#fdae61', label='$D_{low}$ to $D_{high}$')

ax2.set_title('TWL \& Dune\nElevations')
ax2.legend(loc='center',bbox_to_anchor=(0.5,-0.15))
ax2.set_xlabel('Elevation (m AHD)')

# Plot R_high - D_low
ax3.plot(df_beach.R_high - df_beach.dune_toe_z,n,color='#999999')
ax3.axvline(x=0,color='black',linestyle=':')
ax3.set_title('$R_{high}$ - $D_{low}$')
ax3.set_xlabel('Height (m)')
ax3.set_xlim([-2,2])

# Wave height, wave period, beach slope
ax4.plot(df_beach.Hs0, n,color='#377eb8')
ax4.set_title('$H_{s0}$')
ax4.set_xlabel('Sig. wave height (m)')
ax4.set_xlim([3,5])

ax5.plot(df_beach.Tp, n,color='#e41a1c')
ax5.set_title('$T_{p}$')
ax5.set_xlabel('Peak wave period (s)')
ax5.set_xlim([8,14])

ax6.plot(df_beach.tide, n,color='#a6cee3')
ax6.set_title('Tide')
ax6.set_xlabel('Elevation (m AHD)')
ax6.set_xlim([0,2])

ax7.plot(df_beach.beta, n,color='#4daf4a')
ax7.set_title(r'$\beta$')
ax7.set_xlabel('Mean prestorm\nbeach slope')
ax7.set_xlim([0,0.15])

ax8.plot(df_beach.R2, n,color='#6a3d9a')
ax8.set_title(r'$R_{2\%}$')
ax8.set_xlabel('Height (m)')

plt.tight_layout()
f.subplots_adjust(top=0.88)
f.suptitle(beach)


# Print to figure
plt.savefig('07-{}.png'.format(beach), dpi=600, bbox_inches='tight') 

plt.show()
plt.close()